---

# S01E03 : Le système d'importation - Namespaces et scopes

Cyril Desjouy

---


## 1. Quelques rappels sur les noms

Un nom est un **identifieur** appelé couramment variable ou nom de variable. C'est un emplacement nommé permettant d'accéder à un objet en mémoire. Lorsqu'on écrit `a = 1`, on assigne à l'identifieur `a` un objet crée par l'interpréteur dont la valeur est `1` et son adresse en mémoire (son identité) peut être déterminée à l'aide de la fonction built-in `id`.


<div class="alert alert-block alert-info">
Déclarez deux variables <code>a</code> et <code>b</code> égales à 1. Comparez l'identité de ces deux objets.
</div>

Les deux objets ont la même identité. Cela signifie que les identifieurs `a` et `b` référencent le même objet et que l'interpréteur Python n'a pas dupliqué en mémoire l'objet de type entier ayant pour valeur 1.

<div class="alert alert-block alert-info">
Changez maintenant la valeur de <code>b</code> en tapant <code>b = b + 1</code> et comparez à nouveau l'identité de <code>a</code> et <code>b</code>.
</div>

Un nouvel objet de type entier ayant pour valeur 2 a été crée en mémoire. La variable `b` référence maintenant ce nouvel objet.

<div class="alert alert-block alert-info">
Créez maintenant un module que vous nommerez <code>module</code> contenant uniquement l'instruction <code>a = 1</code> puis importez ce module dans le notebook. Comparez l'identité des identifieurs <code>a</code> et <code>module.a</code>. Concluez.
</div>

In [ ]:
import module

id(a) == id(module.a)

**Note:** *Pour accéder à un identifieur d'un module, on le **préfixe** par le nom du module tel qu'il a été importé : `module.a`.*

## 2. Namespaces et scopes

Nous avons déjà abordé la notion de ***namespace*** précédemment lors de l'étude des modules. Pour rappel, un ***namespace*** est une conteneur de noms référençant des objets. Il est important d'insister sur le fait  qu'un namespace ne contient pas les objets, mais juste les références vers ces objets, i.e. les noms. Notons d'ailleurs que comme vu précédemment, il est possible d'avoir plusieurs noms, **pouvant être répartis dans plusieurs namespaces**, référençant le même objet. 

Les ***namespaces*** sont crées par les modules, les fonctions, les classes, ... Plusieurs ***namespaces*** peuvent coexister au même moment mais sont totalement isolés les uns des autres. Ceci permet d'avoir le même nom dans différents namespaces sans provoquer de collision. Par exemple:

In [1]:
reset -f

In [ ]:
import numpy

class cls:
    def __init__(self):
        self.e = 'class'
        
def fct1():
    e = 'fct1'
    return e

def fct2():
    e = 'fct2'
    return e

if __name__ == '__main__':

    e = 'global'

    print('From numpy:', numpy.e)
    print('From cls:', cls().e)
    print('From fct1:', fct1())
    print('From fct2:', fct2())
    print('From program:', e)


Le nom `e` est défini dans le module `numpy`, dans la classe `cls`, dans les fonctions `fct1` et `fct2` et au niveau du programme principal sans que cela ne provoque de collision. Cela est possible grâce aux *namespaces*. 

Même s'il est possible d'avoir plusieurs namespaces défini au même moment, il n'est pas forcement possible d'accéder à tous ces namespaces depuis n'importe quelle partie du programme. On parle alors de ***scope*** (de portée). Le ***scope*** est la portion du programme depuis laquelle il est possible d'accéder à un namespace sans utiliser de préfixe (le préfixe peut être un nom d'un module par exemple : `numpy.e`, ou d'un instance de classe, par exemple `cls().e` comme vu précédemment).

Sous Python, il existe 4 types de namespaces qui ont chacun leur propre ***scope***:

* **Local:** Noms qui sont définis dans une fonction.
* **Enclosed:** Noms qui sont définis dans une **closure** (i.e. une fonction dans une fonction).
* **Global:** Noms qui sont assignés au niveau le plus élevé dans un fichier, par exemple dans votre programme principal ou dans votre module.
* **Built-in:** Noms qui sont les built-ins Pythons (comme `print`, `return`, `import`, ...). Ce namespace est crée quand l'interpréteur Python démarre et existe jusqu'à sa fermeture.

Ces différents scopes sont illustrés sur la figure 1. 

```
______________________________________________________________
|######################### Built-in #########################|
|                                                            |
|    _____________________________________________________   |
|    |############## Global (module level) ##############|   |
|    |                                                   |   |
|    |   _____________________________________________   |   |
|    |   |##### Enclosed (function in function) #####|   |   |
|    |   |                                           |   |   |
|    |   |  ______________________________________   |   |   |
|    |   |  |###### Local (function level) ######|   |   |   |
|    |   |  |                                    |   |   |   |
|    |   |  |____________________________________|   |   |   |
|    |   |___________________________________________|   |   |
|    |___________________________________________________|   |
|____________________________________________________________|
              Fig. 1: Organisation of the namespace
```

Les initiales de ces 4 ***namespaces/scopes*** forment la régle **LEGB** (<b>L</b>ocal, <b>E</b>nclosed, <b>G</b>lobal, <b>B</b>uilt-in) qui impose l'ordre dans lequel doit s'effectuer la recherche de noms dans les namespaces. 

La régle **LEGB** se formalise de la manière suivante:

* Le scope le plus bas est **Local**, le plus haut est **Built-in**
* Les scopes les plus bas peuvent toujours accéder aux scopes les plus hauts
* Les scopes les plus haut ne peuvent jamais ***directement*** accéder aux scopes les plus bas

C'est parce que le scope le plus haut est **Built-in** que les fonctions built-in sont disponibles dans n'importe quelle partie du programme. Pour illustrer ces propos, considérons un ***namespace global***. Vous pouvez y créer des identifieurs référençant des objets et également utiliser des noms du ***namespace Built-in***. Sans ***namespace global*** vous ne pourriez pas écrire ceci:

```python  
msg = "global"     # msg defined in a global namespace
print(msg)         # In the global namespace, you can access "print" function (Built-in namespace)
```

Les fonctions ont un namespace séparé qui est un ***namespace local***. Chaque fonction à son propre *namespace*.

```python
def var_from():
    msg = "local"  # msg defined in a local namespace
    print(msg)     # In local namespace, you can also access "print" function (Built-in namespace)

var_from()         # displays "local"
print(msg)         # msg not defined in the global namespace, so print function raises NameError
```

Comme le montre cet exemple, il est possible d'accéder à la fonction `var_from` qui est définie dans le ***namespace global***, mais pas à `msg` qui est défini dans le ***namespace local*** de la fonction! Il est possible par contre d'accéder au ***namespace global*** depuis le ***namespace local*** de la fonction comme le montre l'exemple suivant:

```python
def var_from():
    print(msg)      # msg not defined locally

msg = "global"
var_from()          # but var_from displays "global"
```

Dans cet exemple, lorsque l'interpréteur Python évalue la fonction `var_from`, il cherche l'identifieur `msg` au niveau du ***namespace local*** de la fonction mais ne le trouve pas. Il suit alors la règle **LEGB** pour parcourir les *namespaces* suivants à la recherche de `msg`. Il n'y a ici pas de ***namespace enclosed***, il cherche donc dans le ***namespace global*** et trouve finalement l'identifieur `msg` qui référence l'objet `'global'`.

Lorsqu'une fonction ***enferme*** une autre fonction, on parle de ***enclosing function***. Ce type de fonction possède un *namespace* propre appelé ***enclosed namespace***. 

<div class="alert alert-block alert-info">
Considérons les deux fonctions <code>outer</code> et <code>inner</code> imbriquées ci-dessous. Exécutez les deux cellules suivantes:
</div>

In [ ]:
reset -f

In [ ]:
def outer():           # Enclosed
    msg = "out!"       
    def inner():
       msg = "in!"     # Local
       print('called from inner:', msg)
    inner()
    print('called from outer:', msg)

# Global
msg = 'global'
outer()
print('called from global:', msg)

<div class="alert alert-block alert-info">
<ul>
    <li> Commentez la ligne <code>msg = "in!"</code> puis exécuter le code précédent.</li>
    <li> Commentez également la ligne <code>msg = "out!"</code> puis exécuter à nouveau.</li>
    <li> Concluez. </li>
</ul>
</div>

Comme vous avez pu le constater, lorsque l'instruction `msg = "in!"` est commentée, `msg` est égal à `'out!'` dans la fonction `inner`. L'interpréteur Python cherche en effet `msg` localement dans la fonction `inner` mais ne le trouve pas. Il suit alors la règle **LEGB** en remontant au niveau **Enclosed** et trouve alors une variable `msg`.

Lorsque les instructions `msg = 'in!'` et `msg = 'out!'` sont commentées, l'interpréteur ne trouve la variable `msg` ni dans `inner`, ni dans `outer`. Il suit alors à nouveau la règle **LEGB** et remonte  au niveau du ***namespace global*** où il trouve `msg = 'global'`. L'identifieur `msg` référence alors l'objet `'global'` dans les fonctions `outer` et `inner`.

## 3. Les instructions `global` et `nonlocal`


Comme nous l'avons vu précédemment il est possible d'accéder aux *namespaces* de plus haut niveau ***directement*** (sans préfixe) suivant la règle **LEGB**. Les *namespaces* de plus bas niveaux peuvent aussi partager des références avec les *namespaces* de plus haut niveau à l'aide des instructions:

* `nonlocal` : précise que les identifieurs listées font **référence** aux identifieurs déclarées précédemment, dans le ***scope*** le plus bas entourant l'instruction, **à l'exception des identifieurs globaux**,
* `global` : précise que les identifieurs listés doivent êtres interprétés comme globaux.


### 3.1. L'instruction `nonlocal`

<div class="alert alert-block alert-info">
Afin d'illustrer le fonctionnement de l'instruction <code>nonlocal</code>, exécutez les deux cellules suivantes:
</div>

In [ ]:
reset -f

In [ ]:
def outer():             # Enclosed
    msg = "out!"
    def inner():         # Local
        nonlocal msg
        msg = 'in!'
        print('called from inner:', msg)
    inner()
    print('called from outer:', msg)

# Global
outer()
print('called from global:', msg)

Ceci peut paraître un peu déroutant mais la variable `msg` référence maintenant :

* l'objet `'in!'` dans le ***namespace local*** de `inner`,
* l'objet `'in!'` dans le ***namespace enclosed*** de `outer`,
* rien dans le ***namespace global*** (non défini).

Lors de l'exécution de la fonction `inner`, l'identifieur `msg` est déclaré comme `nonlocal`. Il référence localement l'objet `'in!'`, mais son ***scope*** (sa portée) est étendu au namespace de plus bas niveau l'entourant c'est à dire celui de la fonction `outer`. Lors de l'exécution de `outer`:
* l'identifieur `msg` référence l'objet `'out!'` à la ligne 2,
* puis la fonction inner est définie puis appelée à la ligne 7,
* l'identifieur `msg` référence alors maintenant l'objet `'in!'` de manière non locale (impactant aussi le namespace supérieur, celui de `outer`),
* à la ligne 8, la fonction <code>print</code> est appelé sur l'identifieur `msg` qui référence également l'objet `'in!'` dans `outer`.

Notons que l'instruction `nonlocal` **n'étend pas le *scope* de `msg` au niveau global**. La variable `msg` n'est donc pas définie dans le namespace global, ce qui lève l'exception `NameError`. 

<div class="alert alert-block alert-info">
Inversez maintenant les lignes <b>7</b> et <b>8</b> et concluez.
</div>

### 3.2. L'instruction `global`

<div class="alert alert-block alert-info">
Afin d'illustrer le fonctionnement de l'instruction <code>global</code>, exécutez les deux cellules suivantes:
</div>

In [ ]:
reset -f

In [ ]:
def outer():           # Enclosed
    msg = "out!"
    def inner():       # Local
        global msg
        msg = "in!"
        print('called from inner:', msg)
    inner()
    print('called from outer:', msg)

# Global
outer()                
print('called from global:', msg)

Comme vous l'aurez remarqué, la variable `msg` référence maintenant :

* l'objet `'in!'` dans le ***namespace local*** de `inner`,
* l'objet `'out!'` dans le ***namespace enclosed*** de `outer`,
* l'objet `'in!'` dans le ***namespace global***.

Dans la fonction `inner`, l'identifieur `msg` est déclaré comme **global**. L'interpréteur Python cherche l'identifieur `msg` dans le *namespace* courant (***local***) et trouve effectivement celui qui référence l'objet `'in!'`, ligne 5.

Dans la fonction `outer`, lorsque la fonction `print` est exécutée à la ligne 8, l'interpréteur Python cherche l'identifieur `msg` dans le *namespace* courant (***enclosed***) et trouve effectivement celui qui référence l'objet `'out!'`, ligne 2. Les deux identifieurs `msg` définis ligne 2 et 5 font bien partie de deux *namespaces* différents et référencent deux objets différents.

Grâce à l'instruction **global**, La portée de l'identifieur `msg` est étendue jusqu'au ***namespace global*** . L'identifieur `msg` de la ligne 12 référence donc l'objet `'in!'` défini dans `inner`, ligne 5, puisque celui ci est global.


<div class="alert alert-block alert-info">
Commentez l'instruction <code>msg = "out!"</code> de la ligne 2, et exécutez à nouveau le code. Concluez.
</div>

## Résumé

* Le ***namespace Built-in*** est réservé à l'interpréteur Python. Il est essentiellement constitué des fonctions built-in.
* Un ***namespace Global*** est un namespace dans lequel sont déclarés tous les identifieurs au niveau du programme principale ou d'un module.
* Un ***namespace Local*** est crée à chaque appel de fonction. Un identifieur déclaré dans une fonction est seulement accessible depuis cette fonction.
* Dans le cas de fonctions imbriquées, chaque fonction possède son propre namespace. Le namespace de la fonction enfermant une autre fonction est appelé ***Enclosed namespace***.
* Un identifieur peut exister dans plusieurs namespaces. Ces identifieurs référencent alors (généralement) des objets différents. Ceci évite les collisions.
* La portée (***scope***) détermine les parties du programme depuis lesquelles un identifieur peut être accessible.  Selon l'emplacement de l'identifieur dans le programme, la recherche s'effectue dans les différents namespaces dans un ordre spécifique déterminé par la règle **LEGB**.
* L'instruction `nonlocal` est utilisée uniquement dans le cas de fonctions imbriquées. Elle permet d'étendre le ***scope*** d'un identifieur au ***namespace enclosed***.
* L'instruction `global` est classiquement utilisée dans une fonction. Elle permet de définir un identifieur comme faisant partie du ***namespace global***.

## Application: In the depths of a module

<div class="alert alert-block alert-info">
Créer un module nommé <code>module</code> dans lequel la fonction suivante sera implémentée :
</div>

```python
def depths():
    
    dark_depths = 'The holy Graal'
    
```

<div class="alert alert-block alert-info">
Comment accéder à la variable <code>dark_depths</code> depuis un autre fichier (au sein du notebook par exemple) ? Vous pourrez modifier la fonction <code>depth</code> pour y parvenir, mais son comportement devra rester identique (retourne <code>None</code>).
</div>

## Bibiographie

* [Python.org - Simple statements](https://docs.python.org/3.8/reference/simple_stmts.html)
* [Confirm.ch - Namespaces](https://blog.confirm.ch/python-namespaces/)
* [data-flair - Namespace & scopes](https://data-flair.training/blogs/python-namespace-and-variable-scope/)
